# <img style="float: left; padding: 0px 10px 0px 0px;" src="https://upload.wikimedia.org/wikipedia/commons/thumb/8/84/Escudo_de_la_Pontificia_Universidad_Cat%C3%B3lica_de_Chile.svg/1920px-Escudo_de_la_Pontificia_Universidad_Cat%C3%B3lica_de_Chile.svg.png"  width="80" /> MCD3100 - Ciencia de Datos Geoespaciales
**Pontificia Universidad Católica de Chile**<br>
**Magister en Ciencia de Datos**<br>

## Tarea N° 2: Análisis de embalses y precipitaciones con GEE.

## 1. Introducción.

El análisis geoespacial y la percepción remota juegan un rol crítico en la gestión de recursos hídricos, ya que permiten medir y monitorear la evolución espaciotemporal de fuentes naturales de agua, y de condiciones ambientales como precipitaciones y temperaturas. Además, es posible observar y analizar fenómenos como el crecimiento urbano, industrialización y cambios de uso de suelo, lo cuales determinan los patrones de consumo de agua en una determinada región.

En esta Tarea, utilizaremos datos satelitales disponibles en la plataforma Google Engine para evaluar la evolución de ciertas fuentes de agua y la distribución de precipitaciones en la región del Maule de Chile.
    

## 2. Datos.

Para este ejercicio, trabajaremos con el catálogo de datos de Google Earth Engine.




## Problemas.

### 1. Evolución espacio temporal de embalses en la cuenca del río Maule. [12 ptos]

La cuenca del río Maule abarca prácticamente la totalidad de la Región del Maule, tiene como cauces principales a los ríos Maule, Claro y Loncomilla, y cuenta con infraestructura de embalses y canales riego, y de generación hidroeléctrica. Los dos mayores embalses de agua son las represas Colbún y Laguna del Maule.

El objetivo de este ejercicio es cuantificar la evolución espacio temporal de la superficie de agua de los embalses Colbún y Laguna del Maule entre los años 2017 y 2025, utilizando imágenes satelitales de la misión Sentinel 2.

La detección de cuerpos de agua en base a imagénes multiespectrales puede realizarse por ejemplo en base al índice normalizado de diferencia NDWI (normalized difference water index). Como referencia, vea los siguientes artículos:

https://custom-scripts.sentinel-hub.com/custom-scripts/sentinel-2/ndwi/ <br>



**1.1[4 ptos]** Genere la geomediana de  Sentinel 2 para el mes de febrero de cada año, con el menor porcentaje de cobertura de nubes posible, y que capture los embalses Colbún-Machicura y la laguna del Maule. <br>
**1.2[4 ptos]** Para cada año, genere una nueva capa de NDWI, y una máscada binaria para identificar los pixeles que corresponde a cuerpos de agua. <br>

**1.3[2 ptos]** Calcule la superficie de agua total ($A_{agua}$) de cada embalse para cada año, y genere un gráfico de serie de tiempo (año vs. $A_{agua}$). Comente, ¿cómo han evolucionado las principales reservas de agua de la región del Maule en los últimos años? <br>

**1.4[2 ptos]** Genere un split map con las capas de NDWI para los años de *menor y mayor* superficie de agua total de los embalses.

Tip: para visualizar las capas de NDWI, puede ser conveniente utilizar los siguiente parámetros:

`visParams = {'min': -1,'max': 1,'palette': ['green', 'blue']}`




#### Solucion

In [15]:
import pandas as pd
import geopandas as gpd
import numpy as np
import matplotlib.pyplot as plt
import geemap,ee
import matplotlib.colors as colors
from shapely.geometry import shape, box, Point
from matplotlib import colors
import matplotlib.patches as mpatches
import contextily as ctx

import rioxarray as rxr

def mask_s2_clouds(image):
    qa = image.select('QA60')  # Quality band
    cloud_bit_mask = 1 << 10
    cirrus_bit_mask = 1 << 11
    mask = qa.bitwiseAnd(cloud_bit_mask).eq(0).And(
           qa.bitwiseAnd(cirrus_bit_mask).eq(0))
    return image.updateMask(mask).divide(10000)  # Scale reflectance


import ee
ee.Initialize()

BANDS = ['B2','B3','B4','B8']

def mask_s2_scl(img):
    scl = img.select("SCL")
    mask = (scl.neq(3)
              .And(scl.neq(8))
              .And(scl.neq(9))
              .And(scl.neq(10))
              .And(scl.neq(11)))
    return img.updateMask(mask)

base = (ee.ImageCollection('COPERNICUS/S2_SR_HARMONIZED')
        .filterBounds(aoi)
        .filter(ee.Filter.calendarRange(2, 2, 'month'))
        .filter(ee.Filter.lt('CLOUDY_PIXEL_PERCENTAGE', 20))
        .map(mask_s2_scl)
       )

def feb_geomedian_for_year(y):
    y = ee.Number(y).toInt()
    start = ee.Date.fromYMD(y, 2, 1)
    end   = start.advance(1, "month")

    col_y = base.filterDate(start, end).select(BANDS)
    n = col_y.size()

    # Imagen vacía (enmascarada) para que NO rompa la colección
    empty = ee.Image.constant([0,0,0,0]).rename(BANDS).updateMask(ee.Image(0)).clip(aoi)

    img = ee.Image(
        ee.Algorithms.If(
            n.gt(0),
            col_y.reduce(ee.Reducer.geometricMedian(len(BANDS))).rename(BANDS).clip(aoi),
            empty
        )
    )

    return img.set({
        "year": y,
        "month": 2,
        "n_imgs": n,
        "system:time_start": start.millis()
    })

In [2]:
ee.Authenticate()
ee.Initialize(project='ee-erickbarrios3')

#### 1.1[4 ptos] Genere la geomediana de Sentinel 2 para el mes de febrero de cada año, con el menor porcentaje de cobertura de nubes posible, y que capture los embalses Colbún-Machicura y la laguna del Maule.

In [16]:
# vemos si el punto corresponde a Maule
# punto ayudantia = (latitud, longitud)

BANDS = ['B2','B3','B4','B8']


punto_ayudantia = (-35.68, -71.379)
punto_maule =  (-36.0667, -70.5000)

lat, long = -35.68, -71.379
lat_maule, long_maule =  -36.0667, -70.5000

crs = 32719

#maule = gpd.read_parquet('E:/OneDrive - Universidad Católica de Chile/Ciencia de Datos Geoespacial/datos_maule/Cartografía_censo2024_R07_Regional.parquet').to_crs(crs)
#print(maule.crs)
#maule

Se delimita el área de estudio o de interés (AOI) como el rectángulo que envuelve tanto a los embalses Colbún-Machicura como a la laguna del Maule. Se busca capturar esos principales cuerpos de agua, no los ríos que se conectan a ellos.

In [29]:

minx,miny,maxx,maxy = -70.429263,-36.120255, -71.439040, -35.591492, 
xy=[[minx,miny],[maxx,miny],[maxx,maxy],[minx,maxy]]
print(xy)
aoi = ee.Geometry.Polygon(xy)
aoi


# puntos adicionales que no se usan para aoi, solo los tengo como referencia
gpd_punto_ayudantia = gpd.GeoDataFrame(
    {'nombre':["Punto Ayudantia"]},
    geometry=[Point(punto_ayudantia[1], punto_ayudantia[0])],
    crs='EPSG:4326'
).to_crs(crs)

gpd_punto_ayudantia_maule = gpd.GeoDataFrame(
    {'nombre':["Punto Maule"]},
    geometry=[Point(punto_maule[1], punto_maule[0])],
    crs='EPSG:4326'
).to_crs(crs)

[[-70.429263, -36.120255], [-71.43904, -36.120255], [-71.43904, -35.591492], [-70.429263, -35.591492]]


In [30]:
base = (ee.ImageCollection('COPERNICUS/S2_SR_HARMONIZED')
        .filterBounds(aoi)
        .filter(ee.Filter.calendarRange(2, 2, 'month'))
        .filter(ee.Filter.lt('CLOUDY_PIXEL_PERCENTAGE', 20))
        .map(mask_s2_scl)
       )

base

In [35]:
import geemap

m = geemap.Map()

# Mostrar un año de ejemplo
y = 2019
img = feb_geomedian_for_year(y)

# segun https://developers.google.com/earth-engine/datasets/catalog/COPERNICUS_S2_SR_HARMONIZED#bands B4,B3,B2 son el Red, Green y Blue respectivamente
viz_rgb = {"bands": ["B4","B3","B2"], "min": 0, "max": 3000}
viz_nir = {"bands": ["B8"], "min": 0, "max": 3000}

m.centerObject(aoi, 10)
m.addLayer(img, viz_rgb, f"Feb {y} RGB")
m.addLayer(img, viz_nir, f"Feb {y} NIR", False)
m.addLayer(aoi, {}, "AOI", True)
m

Map(center=[-35.85663567340677, -70.93415150000017], controls=(WidgetControl(options=['position', 'transparent…

In [36]:
# Agrupamos a una imagen por anio
years = ee.List.sequence(2018, 2024)
geomedianas_febrero = ee.ImageCollection(years.map(feb_geomedian_for_year))

In [37]:
geomedianas_febrero

In [38]:
import geemap

m = geemap.Map()
m.centerObject(aoi, 10)

img_2019 = geomedianas_febrero.filter(ee.Filter.eq("year", 2019)).first()

m.addLayer(img_2019, {"bands":["B4","B3","B2"], "min":0, "max":3000}, "Feb 2019 RGB")
m.addLayer(img_2019, {"bands":["B8"], "min":0, "max":3000}, "Feb 2019 NIR", False)
m.addLayer(aoi, {}, "AOI", True)
m

Map(center=[-35.85663567340677, -70.93415150000017], controls=(WidgetControl(options=['position', 'transparent…

Se generó una ImageCollection compuesta por imágenes anuales, donde cada imagen corresponde a la geomediana multivariada de Sentinel-2 para el mes de febrero, permitiendo analizar de forma consistente la evolución temporal de los cuerpos de agua en el área de estudio.

In [39]:
# validando si la geomediana tiene info
print(f"Años disponibles: {geomedianas_febrero.size().getInfo()}")
print(f"Años: {geomedianas_febrero.aggregate_array("year").getInfo()}")
print(f"Imágenes por año: {geomedianas_febrero.aggregate_array("n_imgs").getInfo()}")

Años disponibles: 7
Años: [2018, 2019, 2020, 2021, 2022, 2023, 2024]
Imágenes por año: [3, 16, 20, 15, 22, 22, 20]


#### 1.2[4 ptos] Para cada año, genere una nueva capa de NDWI, y una máscada binaria para identificar los pixeles que corresponde a cuerpos de agua.

Como referencia, los rangos importantes para NDWI son:

| Rango de NDWI | Interpretación |
|--------------|----------------|
| **0.2 – 1.0** | Superficie de agua (cuerpos de agua abiertos) |
| **0.0 – 0.2** | Inundación, humedad del suelo |
| **−0.3 – 0.0** | Sequía moderada, superficies no acuosas |
| **−1.0 – −0.3** | Sequía intensa, superficies no acuosas |

In [81]:
image1=ee.Image(images[0])
image1=mask_s2_clouds(image1)

image2=ee.Image(images[1])
image2=mask_s2_clouds(image2)

# Sentinel-2 NDWI = (B03 - B08) / (B03 + B08)
ndwi1= image1.normalizedDifference(['B3','B8'])
ndwi2= image2.normalizedDifference(['B3','B8'])

In [88]:
Map = geemap.Map(center=[lat, long], zoom=9)
vis_params = {"min": 0, "max": 3000, "bands": ["B4", "B3", "B2"]}
ndwiParams = {'min': -1,'max': 1,'palette': ['green', 'blue']}


Map.addLayer(im0, vis_params,name='Image1')
Map.addLayer(im1, vis_params,name='Image2')
Map.addLayer(ndwi1, ndwiParams,name='NDWI1')
Map.addLayer(ndwi2, ndwiParams,name='NDWI2')
Map.addLayer(aoi,name='aoi',vis_params={'color':'red'},shown=False)
Map

Map(center=[-35.68, -71.379], controls=(WidgetControl(options=['position', 'transparent_bg'], position='toprig…

### 2. Análisis de patrones de precipitaciones. [6 ptos]

La principal fuente de alimentación de las reservas de agua en la cuenca del Maule son las precipitaciones. Éstas pueden ser registradas mediante sensores, pero la densidad espacial de estaciones metereológicas suele ser baja, por lo que se complementa con estimaciones obtenidas a partir de observaciones satelitales en bandas infra-rojas. Por ejemplo, *Climate Hazards Group InfraRed Precipitation with Station data (CHIRPS)* provee un dataset de precipitaciones cuasi-global desde 1981 al presente, disponibles a través de la plataforma Google Earth Engine. Los datos están disponibles a escala diaria (CHIRPS/DAILY), y a escala de 5 días (CHIRP/PENTAD).

El objetivo de este ejercicio, es estimar las precipitaciones totales obtenidas de  datasets grillados como CHIRP.


**Nota:** Como referencia para este ejercicio, le puede ser de utilidad el siguiente ejemplo:
https://spatialthoughts.com/2020/10/28/rainfall-data-gee/


**2.1[3 ptos]**  De la colección [CHIRPS/PENTAD](https://developers.google.com/earth-engine/datasets/catalog/UCSB-CHG_CHIRPS_PENTAD), obtenga y visualize un raster con el total de precipitaciones mensuales para el mes de julio 2020 en la región del Maule.

* En GEE, Seleccione las imágenes correspondientes a la región del Maule, para el mes de julio 2020 (son 5 o 6 imágenes). Para esto, filtre la colección de imágenes por fecha (`filterDates`) y región (`filterBounds`).
* Combine (sume) todas las imágenes en un único raster, que representará las precipitaciones totales para el mes estudiado (en mm, para cada pixel).
* Recorte (clip) la imagen total por el polígono de la región del Maule.

**2.2[2 ptos]** Genere una visualización del raster de precipationes totales.

**2.3[1 pto]** Calcule la suma de precipitaciones totales para la región del Maule para el mes de julio 2020.